# 参照 Reference
- [pip prophet](https://pypi.org/project/prophet/)
- PROPHET document [Saturating Forecasts](https://facebook.github.io/prophet/docs/saturating_forecasts.html)
- [【トリビアのDelta Lake】#4 Spark DataFrameの変換チートシートを作りました](https://qiita.com/yuulian/items/836fad4aab6c7cf19ed1)

# Saturating Forecasts 飽和予測
## 成長予測
デフォルトでは、プロフェットは予測に線形モデルを使用します。成長を予測する場合、通常達成可能な最大ポイントがあります：市場規模、人口規模などです。これはキャリング・キャパシティと呼ばれ、予測はこのポイントで飽和するはずです。<br>
<br>
プロフェットでは、キャリング・キャパシティを指定した[ロジスティック成長](https://en.wikipedia.org/wiki/Logistic_function)トレンドモデルを使って予測を行うことができます。ウィキペディアの[R（プログラミング言語）](https://en.wikipedia.org/wiki/R_%28programming_language%29)ページへのアクセス数のログで説明します：

In [40]:
import pyspark
from delta import *
from delta.tables import *
from pyspark.sql.functions import *
from pyspark.sql.types import *

import pandas as pd
from prophet import Prophet

from prophet.plot import plot_plotly, plot_components_plotly, add_changepoints_to_plot

builder = pyspark.sql.SparkSession.builder.appName("MyApp") \
  .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") \
  .config("spark.sql.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog")

spark = configure_spark_with_delta_pip(builder).getOrCreate()
spark.conf.set("spark.sql.debug.maxToStringFields", 1000)

In [41]:
workspace = "/workspace"
file_name = "example_wp_log_peyton_manning"
file_ext = ".csv"
data_path = workspace + "/try_prophet/data/" + file_name + file_ext
delta_table_name = "peyton_manning"
delta_table_path = workspace + "/tables/" + delta_table_name
cap_max_value = 8.5
cap_min_value = 6
cap_floor_value = 1.5

In [42]:
# トレーニングデータセットの構造
peyton_manning_schema = StructType([
  StructField('ds', DateType()),
  StructField('y', FloatType())
  ])

# トレーニングファイルをデータフレームに読み込み
peytonDf = spark.read\
  .option("delimiter", ",")\
  .option("header", "true")\
  .schema(peyton_manning_schema)\
  .csv(data_path)

# データフレームをPandas形式に変換する
pandasDf = peytonDf.toPandas()

print("----------------------------------------------------------------------------------------")
print("データを表示")
print("----------------------------------------------------------------------------------------")
pandasDf.head()

----------------------------------------------------------------------------------------
データを表示
----------------------------------------------------------------------------------------


ds         y
0  2007-12-10  9.590761
1  2007-12-11  8.519590
2  2007-12-12  8.183677
3  2007-12-13  8.072468
4  2007-12-14  7.893572

キャリング・キャパシティをカラム・`cap`で指定しなければならない。ここでは特定の値を仮定するが、これは通常、市場規模に関するデータや専門知識を用いて設定されるだろう。

In [43]:
pandasDf['cap'] = cap_max_value
pandasDf.head()

ds         y  cap
0  2007-12-10  9.590761  8.5
1  2007-12-11  8.519590  8.5
2  2007-12-12  8.183677  8.5
3  2007-12-13  8.072468  8.5
4  2007-12-14  7.893572  8.5

注意すべき重要な点は、`cap`はデータフレーム内のすべての行に対して指定されなければならないこと、そして一定である必要はないことである。市場規模が成長している場合、`cap`は増加系列にすることができます。<br>
次に、ロジスティック成長を指定する追加引数を渡す以外は、前と同じようにモデルを当てはめます：

In [44]:
m = Prophet(growth='logistic') # インスタンスを作成する ロジスティック成長を指定する
m.fit(pandasDf)                # fitメソッドで学習する

06:40:06 - cmdstanpy - INFO - Chain [1] start processing
06:40:06 - cmdstanpy - INFO - Chain [1] done processing


前述と同様に将来予測のためのデータフレームを作成するが、ただし、将来におけるキャパシティも指定しなければならない。ここでは、容量を履歴と同じ値で一定に保ち、5年先を予測する：

In [45]:
future = m.make_future_dataframe(periods=1826) # 予測用のデータフレームを指定期間分作成する。
future['cap'] = cap_max_value                      # capを追加
future.tail()                                  # 中身の確認

ds  cap
4726 2021-01-15  8.5
4727 2021-01-16  8.5
4728 2021-01-17  8.5
4729 2021-01-18  8.5
4730 2021-01-19  8.5

In [46]:
forecast = m.predict(future) # predictメソッドで予測を行う
forecast.tail()              # 中身の確認


ds     trend  cap  yhat_lower  yhat_upper  trend_lower  \
4726 2021-01-15  3.951254  8.5    3.362952    6.232836     2.661798   
4727 2021-01-16  3.948480  8.5    3.215697    6.108908     2.658697   
4728 2021-01-17  3.945707  8.5    3.551220    6.375127     2.655596   
4729 2021-01-18  3.942934  8.5    3.841832    6.862324     2.652496   
4730 2021-01-19  3.940161  8.5    3.706732    6.669183     2.649399   

      trend_upper  additive_terms  additive_terms_lower  additive_terms_upper  \
4726     5.265025        0.914762              0.914762              0.914762   
4727     5.263513        0.694451              0.694451              0.694451   
4728     5.262000        1.076873              1.076873              1.076873   
4729     5.260487        1.402303              1.402303              1.402303   
4730     5.258974        1.191228              1.191228              1.191228   

        weekly  weekly_lower  weekly_upper    yearly  yearly_lower  \
4726 -0.069683     -0.069683     -0.069683  0.984445      0.984445   
4727 -0.312960     -0.312960     -0.312960  1.007411      1.007411   
4728  0.047392      0.047392      0.047392  1.029481      1.029481   
4729  0.351867      0.351867      0.351867  1.050436      1.050436   
4730  0.121216      0.121216      0.121216  1.070012      1.070012   

      yearly_upper  multiplicative_terms  multiplicative_terms_lower  \
4726      0.984445                   0.0                         0.0   
4727      1.007411                   0.0                         0.0   
4728      1.029481                   0.0                         0.0   
4729      1.050436                   0.0                         0.0   
4730      1.070012                   0.0                         0.0   

      multiplicative_terms_upper      yhat  
4726                         0.0  4.866016  
4727                         0.0  4.642931  
4728                         0.0  5.022580  
4729                         0.0  5.345236  
4730                         0.0  5.131389

In [47]:
plot_plotly(m, forecast, xlabel='日付', ylabel='値')

ロジスティック関数は0を暗黙の最小値としており、容量で飽和するのと同じように0で飽和する。異なる飽和最小値を指定することも可能です。

# 飽和最小値
ロジスティック成長モデルは、飽和最小値も扱うことができます。これは、`cap`列が最大値を指定するのと同じように、列`floor`で指定されます：

In [48]:
pandasDf['y'] = 10 - pandasDf['y']
pandasDf['cap'] = cap_min_value
pandasDf['floor'] = cap_floor_value
future['cap'] = cap_min_value
future['floor'] = cap_floor_value
m = Prophet(growth='logistic')
m.fit(pandasDf)
forecast = m.predict(future)
plot_plotly(m, forecast, xlabel='日付', ylabel='値')

06:40:11 - cmdstanpy - INFO - Chain [1] start processing
06:40:11 - cmdstanpy - INFO - Chain [1] done processing


最小値が飽和するロジスティック成長トレンドを使用するには、最大容量も指定しなければならない。